In [25]:
import pandas as pd
from goessolarretriever import Retriever, Satellite, Product
from glob import glob
from datetime import datetime
import numpy as np
from astropy.io import fits
import os
import matplotlib.pyplot as plt
%matplotlib notebook

First we specify the satellite, product, and time interval to retrive. We can search for all the data in that time interval. 

*Note: the current time interval will take a while. Decrease the window to save time.*

In [26]:
satellite = Satellite.GOES16
product = Product.suvi_l2_ci195

start = datetime(2019, 2, 1)
end = datetime(2019, 3, 1)

r = Retriever()
df = r.search(satellite, product, start, end)

Now, we can inspect the table and see how many entries there are. 

In [27]:
df

file_name          date_begin  \
0     dr_suvi-l2-ci195_g16_s20190201T000000Z_e201902... 2019-02-01 00:00:00   
1     dr_suvi-l2-ci195_g16_s20190201T000400Z_e201902... 2019-02-01 00:04:00   
2     dr_suvi-l2-ci195_g16_s20190201T000800Z_e201902... 2019-02-01 00:08:00   
3     dr_suvi-l2-ci195_g16_s20190201T001200Z_e201902... 2019-02-01 00:12:00   
4     dr_suvi-l2-ci195_g16_s20190201T001600Z_e201902... 2019-02-01 00:16:00   
...                                                 ...                 ...   
7957  dr_suvi-l2-ci195_g16_s20190301T234000Z_e201903... 2019-03-01 23:40:00   
7958  dr_suvi-l2-ci195_g16_s20190301T234400Z_e201903... 2019-03-01 23:44:00   
7959  dr_suvi-l2-ci195_g16_s20190301T234800Z_e201903... 2019-03-01 23:48:00   
7960  dr_suvi-l2-ci195_g16_s20190301T235200Z_e201903... 2019-03-01 23:52:00   
7961  dr_suvi-l2-ci195_g16_s20190301T235600Z_e201903... 2019-03-01 23:56:00   

                date_end         date_edited file_size  \
0    2019-02-01 00:04:00 2019-02-01 00:10:00      1.4M   
1    2019-02-01 00:08:00 2019-02-01 00:14:00      1.4M   
2    2019-02-01 00:12:00 2019-02-01 00:18:00      1.4M   
3    2019-02-01 00:16:00 2019-02-01 00:22:00      1.4M   
4    2019-02-01 00:20:00 2019-02-01 00:26:00      1.4M   
...                  ...                 ...       ...   
7957 2019-03-01 23:44:00 2019-03-01 23:50:00      1.3M   
7958 2019-03-01 23:48:00 2019-03-01 23:54:00      1.3M   
7959 2019-03-01 23:52:00 2019-03-01 23:58:00      1.3M   
7960 2019-03-01 23:56:00 2019-03-02 00:02:00      1.3M   
7961 2019-03-02 00:00:00 2019-03-02 00:06:00      1.3M   

                                                    url  
0     https://data.ngdc.noaa.gov/platforms/solar-spa...  
1     https://data.ngdc.noaa.gov/platforms/solar-spa...  
2     https://data.ngdc.noaa.gov/platforms/solar-spa...  
3     https://data.ngdc.noaa.gov/platforms/solar-spa...  
4     https://data.ngdc.noaa.gov/platforms/solar-spa...  
...                                                 ...  
7957  https://data.ngdc.noaa.gov/platforms/solar-spa...  
7958  https://data.ngdc.noaa.gov/platforms/solar-spa...  
7959  https://data.ngdc.noaa.gov/platforms/solar-spa...  
7960  https://data.ngdc.noaa.gov/platforms/solar-spa...  
7961  https://data.ngdc.noaa.gov/platforms/solar-spa...  

[7962 rows x 6 columns]

We can resample to get one image for every 4 hours and then examine the list. 

In [28]:
times = pd.DataFrame(list(zip(df['file_name'].array, df['url'].array)), index=df['date_begin'], columns=['file_name', 'url'])

In [29]:
times = times.resample("4h").asfreq().replace(np.nan, '', regex=True)

In [30]:
times

file_name  \
date_begin                                                               
2019-02-01 00:00:00  dr_suvi-l2-ci195_g16_s20190201T000000Z_e201902...   
2019-02-01 04:00:00  dr_suvi-l2-ci195_g16_s20190201T040000Z_e201902...   
2019-02-01 08:00:00  dr_suvi-l2-ci195_g16_s20190201T080000Z_e201902...   
2019-02-01 12:00:00  dr_suvi-l2-ci195_g16_s20190201T120000Z_e201902...   
2019-02-01 16:00:00  dr_suvi-l2-ci195_g16_s20190201T160000Z_e201902...   
...                                                                ...   
2019-03-01 04:00:00  dr_suvi-l2-ci195_g16_s20190301T040000Z_e201903...   
2019-03-01 08:00:00  dr_suvi-l2-ci195_g16_s20190301T080000Z_e201903...   
2019-03-01 12:00:00  dr_suvi-l2-ci195_g16_s20190301T120000Z_e201903...   
2019-03-01 16:00:00  dr_suvi-l2-ci195_g16_s20190301T160000Z_e201903...   
2019-03-01 20:00:00  dr_suvi-l2-ci195_g16_s20190301T200000Z_e201903...   

                                                                   url  
date_begin                                                              
2019-02-01 00:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-02-01 04:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-02-01 08:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-02-01 12:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-02-01 16:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
...                                                                ...  
2019-03-01 04:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-03-01 08:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-03-01 12:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-03-01 16:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  
2019-03-01 20:00:00  https://data.ngdc.noaa.gov/platforms/solar-spa...  

[174 rows x 2 columns]

Finally, we retrieve all the images requested and save them in the specified folder. 

In [31]:
r.retrieve(times, "suvi_movie/data/")

174it [02:13,  1.30it/s]


In [32]:
times.to_csv("suvi_movie/times.csv")

To examine our results, we can make a movie of the images. 

In [33]:
def my_scale(img, power=0.25):
    return np.sign(img) * np.power(np.abs(img), power)

i = 0
for date, row in times.iterrows():
    if row['url']: 
        try:
            img = fits.open(os.path.join("suvi_movie/data/", row['file_name']))
            data = my_scale(img[1].data)
        except:
            data = np.zeros((1280, 1280))
    else:
        data = np.zeros((1280,1280))
    date_str = datetime.strftime(date, "%Y-%m-%d %H:%M")
    fig, ax = plt.subplots()
    ax.imshow(data, vmin=0, vmax=1.2, origin='lower')
    ax.set_axis_off()
    ax.set_title(date_str)
    fig.savefig("suvi_movie/pngs/image{:04d}.png".format(i))
    plt.close()
    i+=1

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Run the following to make movies:

-```ffmpeg -framerate 10 -i image%04d.png -s:v 1280x720 -c:v h264_nvenc -profile:v high -crf 20 -pix_fmt yuv420p ../slow.mp4```

-```ffmpeg -framerate 60 -i image%04d.png -s:v 1280x720 -c:v h264_nvenc -profile:v high -crf 20 -pix_fmt yuv420p ../fast.mp4```